# Import Block

In [1]:
import pandas as pd
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import sent_tokenize, word_tokenize
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('stopwords')
import tensorflow as tf
from sklearn.model_selection import train_test_split
from transformers import AutoTokenizer, TFGPT2LMHeadModel, AutoModelWithLMHead, TextDataset, DataCollatorForLanguageModeling, Trainer, TrainingArguments, pipeline
from tqdm import tqdm
tqdm.pandas()
import spacy
import torch
import accelerate
import random
import contractions
import math
import re
import os
import numpy as  np
import warnings

#tokenizer = AutoTokenizer.from_pretrained('gpt2-medium')
# tokenizer.bos_token = '<|start|>'
# tokenizer.eos_token ='<|end|>'
# tokenizer.pad_token_id = tokenizer.eos_token_id
# model = TFGPT2LMHeadModel.from_pretrained('gpt2-medium')

tokenizer = AutoTokenizer.from_pretrained('gpt2') 
model = AutoModelWithLMHead.from_pretrained('gpt2')


warnings.filterwarnings(action = 'ignore')
stopwords = set(stopwords.words('english'))
stopwords.remove('no')
stopwords.remove('not')
stopwords.remove('nor')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\avamc_srsebwe\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\avamc_srsebwe\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\avamc_srsebwe\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
d:\anaconda\envs\ms\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
d:\anaconda\envs\ms\lib\site-packages\transformers\models\auto\modeling_auto.py:1352: FutureWarning: The class `AutoModelWithLMHead` is deprecated and will be removed in a future version. Please use `AutoModelForCausalLM` for causal language models, `AutoModelForMa

In [4]:
torch.cuda.is_available()

False

In [6]:
dataset = pd.read_csv('./dataset/dataset.csv')

# train = train.truncate(before=750000, after=850000)
# train = train.sample(frac=.1, random_state = 8)

#drop na cells
#dataset = dataset.dropna()
dataset.isna().sum()
dataset = dataset[dataset['humor'] == True]

jokeList = dataset['text'].to_list()


In [224]:
dataset.head()

text  humor
2   What do you call a turtle without its shell? d...   True
6   What is a pokemon master's favorite kind of pa...   True
7   Why do native americans hate it when it rains ...   True
9       My family tree is a cactus, we're all pricks.   True
13  How are music and candy similar? we throw away...   True

In [7]:
jokeDataset = {}
maxLen = 64
batch_size = 1
shuffle = True


jokeList = ['<|start|>' + joke + '<|end|>' for joke in jokeList]

encodings = [tokenizer.encode_plus(
    joke,
    None,
    add_special_tokens=True,
    max_length = maxLen,
    pad_to_max_length = True,
    truncation=True,
    return_token_type_ids=True,
    return_attention_mask=True,
    return_tensors = 'tf'
    )
             for joke in jokeList]

ids = [x['input_ids'] for x in encodings]
masks = [x['attention_mask'] for x in encodings]
types = [x['token_type_ids'] for x in encodings]

inputs = {}
inputs['input_ids'] = ids
inputs['attention_mask'] = masks
inputs['token_type_ids'] = types

ds = tf.data.Dataset.from_tensor_slices(inputs)

if shuffle:
    ds = ds.shuffle(buffer_size=len(jokeList))

clean_data = ds.batch(batch_size)

KeyboardInterrupt: 

In [245]:
for x in clean_data:
    a, b, c = x['input_ids'], x['attention_mask'], x['token_type_ids']
    print(a[0][0], b[0][0], c[0][0])
    break

tf.Tensor(
[   27    91  9688    91    29  2061   468  1440  7405   290 42675   289
 23130   466    71    11   289 23130   466    71    30   734  2042  3730
  2111   284  4929   281 20932 29847    91   437    91    29 50256 50256
 50256 50256 50256 50256 50256 50256 50256 50256 50256 50256 50256 50256
 50256 50256 50256 50256 50256 50256 50256 50256 50256 50256 50256 50256
 50256 50256 50256 50256], shape=(64,), dtype=int32) tf.Tensor(
[1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0], shape=(64,), dtype=int32) tf.Tensor(
[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0], shape=(64,), dtype=int32)


In [ ]:
for i in clean_data:
    print(i)

In [169]:
for i in clean_data:
    print(i)

{'input_ids': <tf.Tensor: shape=(16, 1, 64), dtype=int32, numpy=
array([[[   27,    91,  9688, ..., 50257, 50257, 50257]],

       [[   27,    91,  9688, ..., 50257, 50257, 50257]],

       [[   27,    91,  9688, ..., 50257, 50257, 50257]],

       ...,

       [[   27,    91,  9688, ..., 50257, 50257, 50257]],

       [[   27,    91,  9688, ..., 50257, 50257, 50257]],

       [[   27,    91,  9688, ..., 50257, 50257, 50257]]])>, 'attention_mask': <tf.Tensor: shape=(16, 1, 64), dtype=int32, numpy=
array([[[1, 1, 1, ..., 0, 0, 0]],

       [[1, 1, 1, ..., 0, 0, 0]],

       [[1, 1, 1, ..., 0, 0, 0]],

       ...,

       [[1, 1, 1, ..., 0, 0, 0]],

       [[1, 1, 1, ..., 0, 0, 0]],

       [[1, 1, 1, ..., 0, 0, 0]]])>, 'token_type_ids': <tf.Tensor: shape=(16, 1, 64), dtype=int32, numpy=
array([[[0, 0, 0, ..., 0, 0, 0]],

       [[0, 0, 0, ..., 0, 0, 0]],

       [[0, 0, 0, ..., 0, 0, 0]],

       ...,

       [[0, 0, 0, ..., 0, 0, 0]],

       [[0, 0, 0, ..., 0, 0, 0]],

       [[0, 0, 

# Model

In [5]:
model.summary()

Model: "tfgpt2lm_head_model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 transformer (TFGPT2MainLaye  multiple                 354823168 
 r)                                                              
                                                                 
Total params: 354,823,168
Trainable params: 354,823,168
Non-trainable params: 0
_________________________________________________________________


# Loss Function and Optimizer

In [6]:
loss_function = tf.losses.SparseCategoricalCrossentropy(from_logits=True)
     
optimizer = tf.keras.optimizers.Adam(learning_rate=1e-5, epsilon=1e-08, clipnorm=1.0) 

# CheckPoint

In [7]:
check_path = './checkpoint'

ckpt = tf.train.Checkpoint(model = model)

ckpt_manager = tf.train.CheckpointManager(ckpt, check_path, max_to_keep=5)

# if a checkpoint exists, restore the latest checkpoint.
if ckpt_manager.latest_checkpoint:
    ckpt.restore(ckpt_manager.latest_checkpoint)
    print("latest checkpoint restored")

latest checkpoint restored


# Training

In [59]:
def train_step(epoch, batch, min, data_dict):
    #print((data_dict['input_ids']))
    with tf.GradientTape() as tape:
        # print(data_dict['input_ids'][0][0])
        # print(data_dict['attention_mask'][0][0])
        # print(data_dict['token_type_ids'][0][0])
        outputs = model(input_ids = data_dict['input_ids'][0], attention_mask = data_dict['attention_mask'][0], token_type_ids = data_dict['token_type_ids'][0])
        
        lm_logits = outputs[0]
        labels = data_dict['input_ids']
        ## For computing loss we remove the last element from logits and 
        ## first from labels. Thus we need the model to learn to predict next
        ## word more confidently among the others. 
        shift_logits = lm_logits[..., :-1, :]
        shift_labels = labels[..., 1:]
    
        loss = loss_function(
            tf.reshape(shift_labels, (-1,)), 
            tf.reshape(shift_logits, (-1, shift_logits.shape[-1])))

    gradients = tape.gradient(loss, model.trainable_variables)    
    optimizer.apply_gradients(zip(gradients, model.trainable_variables))
    if loss < min and loss < 0.5:
        model.save(os.path.join('./models',f"gpt2_{epoch}_{batch}"))

    
    return loss

99, 999

In [60]:
EPOCHS = 1
min = 100000
for epoch in range(EPOCHS):
    for batch, data in (enumerate(clean_data)):
        loss = train_step(epoch, batch, min, data)
        if batch % 100 == 0:
            print('Epoch : {0} Batch : {1} ---- Loss : {2}'.format(epoch+1, batch+1, loss))
  
    ckpt_save_path = ckpt_manager.save()
    print ('Saving checkpoint for epoch {} at {}'.format(epoch+1, ckpt_save_path))

Epoch : 1 Batch : 1 ---- Loss : 1.3652087450027466
Epoch : 1 Batch : 101 ---- Loss : 1.1790915727615356
Epoch : 1 Batch : 201 ---- Loss : 0.8901644349098206
Epoch : 1 Batch : 301 ---- Loss : 0.9869068264961243
Epoch : 1 Batch : 401 ---- Loss : 0.9772112965583801


INFO:tensorflow:Assets written to: ./models\gpt2_0_479\assets


INFO:tensorflow:Assets written to: ./models\gpt2_0_479\assets


Epoch : 1 Batch : 501 ---- Loss : 0.9699894785881042
Epoch : 1 Batch : 601 ---- Loss : 0.6069926023483276
Epoch : 1 Batch : 701 ---- Loss : 1.1099532842636108


INFO:tensorflow:Assets written to: ./models\gpt2_0_716\assets


...

INFO:tensorflow:Assets written to: ./models\gpt2_0_2654\assets


Epoch : 1 Batch : 2701 ---- Loss : 0.9808999300003052


INFO:tensorflow:Assets written to: ./models\gpt2_0_2727\assets


INFO:tensorflow:Assets written to: ./models\gpt2_0_2727\assets


KeyboardInterrupt: 

180 minutes - stopped it manually . hopefully it saves . idk if it did oops
- Epoch : 1 Batch : 1 ---- Loss : 1.1551498174667358
- Epoch : 1 Batch : 101 ---- Loss : 0.8924950957298279
- Epoch : 1 Batch : 201 ---- Loss : 1.0445066690444946
- Epoch : 1 Batch : 301 ---- Loss : 1.2258509397506714
- Epoch : 1 Batch : 401 ---- Loss : 1.313239574432373
- Epoch : 1 Batch : 501 ---- Loss : 1.1019868850708008
- Epoch : 1 Batch : 601 ---- Loss : 1.30625319480896
- Epoch : 1 Batch : 701 ---- Loss : 0.8831945657730103
- Epoch : 1 Batch : 801 ---- Loss : 1.3074332475662231
- Epoch : 1 Batch : 901 ---- Loss : 0.7686089873313904
- Epoch : 1 Batch : 1001 ---- Loss : 0.5327813029289246

51 minutes - stopped cause of error
- Epoch : 1 Batch : 1 ---- Loss : 5.8245038986206055
- Epoch : 1 Batch : 101 ---- Loss : 1.0989317893981934
- Epoch : 1 Batch : 201 ---- Loss : 0.7495436072349548
- Epoch : 1 Batch : 301 ---- Loss : 1.0246530771255493

tested the joke generator after this though. and it seems to be kinda working ? not very funny though 

508 minutes: stopped manually. i forgot to update the min variable. so now i gotta figure out which model is best
Epoch : 1 Batch : 1 ---- Loss : 1.3652087450027466
Epoch : 1 Batch : 101 ---- Loss : 1.1790915727615356
Epoch : 1 Batch : 201 ---- Loss : 0.8901644349098206
Epoch : 1 Batch : 301 ---- Loss : 0.9869068264961243
Epoch : 1 Batch : 401 ---- Loss : 0.9772112965583801
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_479\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_479\assets
Epoch : 1 Batch : 501 ---- Loss : 0.9699894785881042
Epoch : 1 Batch : 601 ---- Loss : 0.6069926023483276
Epoch : 1 Batch : 701 ---- Loss : 1.1099532842636108
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_716\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_716\assets
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_746\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_746\assets
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_756\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_756\assets
Epoch : 1 Batch : 801 ---- Loss : 0.7894040942192078
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_872\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_872\assets
Epoch : 1 Batch : 901 ---- Loss : 1.1121970415115356
Epoch : 1 Batch : 1001 ---- Loss : 1.045320749282837
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_1018\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_1018\assets
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_1028\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_1028\assets
Epoch : 1 Batch : 1101 ---- Loss : 1.3675634860992432
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_1169\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_1169\assets
Epoch : 1 Batch : 1201 ---- Loss : 0.8966301679611206
Epoch : 1 Batch : 1301 ---- Loss : 1.050649881362915
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_1318\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_1318\assets
Epoch : 1 Batch : 1401 ---- Loss : 0.5872712731361389
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_1456\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_1456\assets
Epoch : 1 Batch : 1501 ---- Loss : 1.2013167142868042
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_1596\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_1596\assets
Epoch : 1 Batch : 1601 ---- Loss : 0.7073613405227661
Epoch : 1 Batch : 1701 ---- Loss : 1.0524898767471313
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_1730\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_1730\assets
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_1783\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_1783\assets
Epoch : 1 Batch : 1801 ---- Loss : 1.0663630962371826
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_1855\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_1855\assets
Epoch : 1 Batch : 1901 ---- Loss : 1.2361420392990112
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_1913\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_1913\assets
Epoch : 1 Batch : 2001 ---- Loss : 1.121724247932434
Epoch : 1 Batch : 2101 ---- Loss : 0.575840413570404
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_2131\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_2131\assets
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_2189\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_2189\assets
Epoch : 1 Batch : 2201 ---- Loss : 0.8447523713111877
Epoch : 1 Batch : 2301 ---- Loss : 0.7730249166488647
Epoch : 1 Batch : 2401 ---- Loss : 0.5232420563697815
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_2489\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_2489\assets
Epoch : 1 Batch : 2501 ---- Loss : 0.9592006802558899
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_2581\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_2581\assets
Epoch : 1 Batch : 2601 ---- Loss : 0.6818088889122009
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_2654\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_2654\assets
Epoch : 1 Batch : 2701 ---- Loss : 0.9808999300003052
WARNING:absl:Found untraced functions such as wte_layer_call_fn, wte_layer_call_and_return_conditional_losses, wpe_layer_call_fn, wpe_layer_call_and_return_conditional_losses, dropout_365_layer_call_fn while saving (showing 5 of 584). These functions will not be directly callable after loading.
INFO:tensorflow:Assets written to: ./models\gpt2_0_2727\assets
INFO:tensorflow:Assets written to: ./models\gpt2_0_2727\assets

In [61]:
ckpt_save_path = ckpt_manager.save()
print ('Saving checkpoint for epoch {} at {}'.format(epoch+1, ckpt_save_path))

Saving checkpoint for epoch 1 at ./checkpoint\ckpt-2


Save

In [ ]:
trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=train_dataset,
)

# Generating

In [3]:
epoch = 0
batch = 479
model = TFGPT2LMHeadModel.load(f'./models/gpt2_{epoch}_{batch}')
# load_gpt2(sess,
#               checkpoint='latest',
#               run_name="run1",
#               checkpoint_dir="checkpoint",
#               model_name=None,
#               model_dir='models',
#               multi_gpu=False,
#               reuse=False):

NameError: name 'load_gpt2' is not defined

In [4]:
epoch = 0
batch = 479
model = TFGPT2LMHeadModel.from_pretrained(f'./models/gpt2_{epoch}_{batch}')

OSError: ./models/gpt2_0_479 does not appear to have a file named config.json. Checkout 'https://huggingface.co/./models/gpt2_0_479/None' for available files.

In [51]:
def exploit_best_token_while_exploring(probabilites, exploration_len=5):
    ## Get the top k probabilites indices where k is exploration_len 
    top_indices = np.argpartition(probabilites, -exploration_len)\
                            [-exploration_len:]

    ## Getting top proabilities value
    top_probabilities = probabilites[top_indices]

    ## Normalizing it so that they sum is 1
    top_probabilities = top_probabilities / np.sum(top_probabilities)

    ## Although we choose next token randomly for our options we 
    ## pass the probabilities associated with each to account for the
    ## model's confidence for the token also. 
    choice = np.random.choice(exploration_len, 1, p = top_probabilities)

    ## Return next token id based on choice
    next_token_id = int(top_indices[choice][0])
    return next_token_id

In [52]:
def generate_joke(joke_length = 64):

  ## Begin by appending the START_TOKEN to our current joke
  current_joke = tf.expand_dims(tf.convert_to_tensor(tokenizer.encode('<|start|>')), 0)
  
  for pos in range(joke_length):

    ## Get output of model for the current_joke
    output = model(current_joke)

    ## Getting the logits value from output tuple i.e. (logits)
    logits = output[0]

    ## Logits is of the shape (BATCH, LEN_INPUT) 
    ## So, since batch size is 1 we get 0th index
    ## and the softmax for only the next possible word i.e. -1
    softmax_logits = tf.nn.softmax(logits[0, -1], axis=0).numpy()

    ## Depending on whether we are in initial or final stages of joke
    ## we determine how many options we should explore to make sure we have
    ## variety in jokes generated
    if pos == 0:
      # If we are predicting first word we need maximum exploration
      exploration_len = 50

    elif pos < 4:
      # The next three words have exploration length 15
      exploration_len = 15

    else:
      # As we move further we narrow our exploration length
      exploration_len = 4

    ## Get the token we should append to current joke
    token_to_append = exploit_best_token_while_exploring(softmax_logits, exploration_len)

    ## Append the token to current joke
    current_joke = tf.concat([current_joke, 
                              tf.ones((1,1), dtype = tf.int32)*token_to_append], 
                             axis = 1)
    
    ## In case the token belongs to the END_TOKEN we return it as complete joke
    if token_to_append in tokenizer.encode('<|end|>'):
      return tokenizer.decode(list(tf.squeeze(current_joke).numpy()))
    
  #delete when fixed
  return tokenizer.decode(list(tf.squeeze(current_joke).numpy()))

  ## If we did not get end token it means no joke is formed
  return None

In [53]:
generate_joke()

"<|start|>Do the math on this. It's like you're a kid with a broken leg.<|"

In [54]:
generate_joke()

"<|start|>You have an idea of what you want to do. You just don't know what you're going to get.</|"

In [55]:
generate_joke()

'<|start|>Cats like cats, dogs like dogs, and people like people.<|endoftext|>The following is an excerpt from a lecture by Professors of Philosophy and Religion at the University of California at Berkeley, titled, "The Moral Case for the Use of the Mass." It is a lecture entitled, "A Moral Argument for the Mass'

# the other way

## Text Preprocessing

In [2]:
print(dataset.head())

NameError: name 'dataset' is not defined

In [7]:
def cleanTheData(data):
    #data is one string from df
    # if(len(data)) > 512:
    #     return
    #expand contractions and go to lowercase
    data = contractions.fix(data.lower()) 
    data = re.sub('[^a-z?]', ' ', data)
    #data = data[0:100]
    return data

#quick sample test run
'''
df2= test = pd.read_csv('test.csv')
df2["A"] = df2['Text'].apply(cleanTheData)
df2.head()
'''
        
dataset['text'] = dataset['text'].apply(cleanTheData)

dataset = dataset.dropna()
dataset['text'].to_csv("./dataset/clean.csv")

convert csv to text file and split

In [2]:
clean = pd.read_csv('./dataset/clean.csv')

In [3]:
test = clean[0:math.floor(.5*len(clean))]
train = clean[math.ceil(.5*len(clean)):len(clean)]

In [4]:
len(train)

50000

In [5]:
print(clean['text'][2])

why do native americans hate it when it rains in april? because it brings mayflowers 


In [6]:
train_path = './dataset/train_clean.txt'
test_path = './dataset/test_clean.txt'

# bos = '<|bos|>'
# eos = '<|eos|>'
# pad = '<|pad|>'
# special_tokens_dict = {'eos_token': eos, 'bos_token': bos, 'pad_token': pad}
# tokenizer.add_special_tokens(special_tokens_dict)
#model.resize_token_embeddings(len(tokenizer))

# with open(train_path, "w", encoding='utf-8') as f:
#     for i in train['text']:
#         f.write (tokenizer.special_tokens_map['bos_token'] + i.rstrip() + tokenizer.special_tokens_map['eos_token'] + '\n')
        
# with open(test_path, "w", encoding='utf-8') as f:
#     for i in test['text']:
#         f.write (tokenizer.special_tokens_map['bos_token'] + i.rstrip()  + tokenizer.special_tokens_map['eos_token'] + '\n')

with open(train_path, "w", encoding='utf-8') as f:
    for i in train['text']:
        f.write (tokenizer.bos_token + i.rstrip() + tokenizer.eos_token )
        
with open(test_path, "w", encoding='utf-8') as f:
    for i in test['text']:
        f.write (tokenizer.bos_token + i.rstrip()  + tokenizer.eos_token  )

In [7]:
i = 0
with open(test_path, "r") as read:
    for line in read.readlines():
        i = i+1
        
print(i)

1


In [17]:
print(model.transformer.wte.weight.shape[0])

50257


In [18]:
print( len(tokenizer))

50257


## Control size for testing

In [14]:
train_path = './dataset/train_clean.txt'
test_path = './dataset/test_clean.txt'

s_train_path = './dataset/small_train_clean.txt'
s_test_path = './dataset/small_test_clean.txt'

i = 200
temp = ""
with open(train_path, "r", encoding='utf-8') as read:
    for line in read.readlines():
        if (i == 0):
            continue 
        temp += line
        i = i-1
with open(s_train_path, "w", encoding='utf-8') as f:
    f.write(temp)

i = 200
temp = "" 
with open(test_path, "r", encoding='utf-8') as read:
    for line in read.readlines():
        if (i == 0):
            continue 
        temp += line
        i = i-1
with open(s_test_path, "w", encoding='utf-8') as f:
    f.write(temp)
    
    
data_collator = DataCollatorForLanguageModeling(
    tokenizer = tokenizer, 
    mlm=False)
    
s_train_data = TextDataset(
    tokenizer=tokenizer, 
    file_path=s_train_path, 
    block_size=512)

s_test_data = TextDataset(
    tokenizer=tokenizer, 
    file_path=s_test_path, 
    block_size=512)

In [15]:
len(s_test_data)

1948

In [17]:
model_path = './model-400'
training_args = TrainingArguments(
    output_dir=model_path, #The output directory
    overwrite_output_dir=True, #overwrite the content of the output directory
    num_train_epochs=1, # number of training epochs
    per_gpu_train_batch_size=32, # batch size for training
    per_gpu_eval_batch_size=64,  # batch size for evaluation
    logging_steps = 500, # Number of update steps between two evaluations.
    save_steps=500, # after # steps model is saved
    warmup_steps=500,# number of warmup steps for learning rate scheduler
    )


trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=s_train_data,
    eval_dataset=s_test_data
)


trainer.train() 
trainer.save_model(model_path) 
tokenizer.save_pretrained(model_path)

Using deprecated `--per_gpu_train_batch_size` argument which will be removed in a future version. Using `--per_device_train_batch_size` is preferred.
Using deprecated `--per_gpu_train_batch_size` argument which will be removed in a future version. Using `--per_device_train_batch_size` is preferred.
Using deprecated `--per_gpu_train_batch_size` argument which will be removed in a future version. Using `--per_device_train_batch_size` is preferred.
Using deprecated `--per_gpu_train_batch_size` argument which will be removed in a future version. Using `--per_device_train_batch_size` is preferred.
Using deprecated `--per_gpu_eval_batch_size` argument which will be removed in a future version. Using `--per_device_eval_batch_size` is preferred.



KeyboardInterrupt: 

In [69]:
model_path = './model-20000'

tokenizer = AutoTokenizer.from_pretrained(model_path)
model = AutoModelWithLMHead.from_pretrained(model_path)

text_generator = pipeline(
    'text-generation', 
    model=model, 
    tokenizer=tokenizer,
    do_sample = True
    )

In [75]:
gen_text = text_generator("What do you call", no_repeat_ngram_size=3, repetition_penalty=1.0, max_new_tokens=30)
print(gen_text[0]['generated_text'])

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


What do you call it? Oh, come on, we're going to be living in peace," said the woman. "We're in peace." "Are you living
